In [1]:
# 引入WebDriver包
import datetime
import json
from pathlib import Path
from selenium import webdriver
# 引入WebDriver Keys包
from selenium.webdriver import ActionChains
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.select import Select
import time

# 创建浏览器对象
# driver = webdriver.PhantomJS()

# options = webdriver.ChromeOptions()
driver = webdriver.Chrome()
driver.set_window_size(800, 600)

driver.implicitly_wait(300)

WebDriverException: Message: unknown command: unknown command: session/d560d111975c8b816e5c8a6b487c4003/window/size


In [2]:
driver.get('https://www.cobusgroup.com/home')
time.sleep(1)

In [3]:
# 登录，操作到指定国家、进出口页面、时间 页面

In [4]:
# 文件路径
# dir_path = Path(r'E:\cobus_group\阿根廷\进口\202109')
dir_path = Path(r'E:\cobus_group\危地马拉\进口\202101_202109')
search_hs_code_prefix = ''
over_file = '_over.txt'

# 起始和终止月份
month_start = '1'
month_end = '9'

dir_path.mkdir(parents=True, exist_ok=True)

# 阿根廷
# edit_url = 'https://www.cobusgroup.com/simple-arnI'
# 危地马拉
edit_url = 'https://www.cobusgroup.com/complementaria-guaI'

In [5]:
# 设置分页大小
# page_size_select = driver.find_element_by_xpath('//select[@id="select_paginas"]')
# Select(page_size_select).select_by_value('200')

In [6]:
def find_next_page_btn():
    """
    查找下一页按钮
    :return:
    """
    page_a_list = driver.find_elements_by_xpath('//div[@id="pagina_resultados"]/div/a')
    next_ten_btn_text = 'SIGUIENTE'
    current_page_btn_index = None
    next_ten_btn = None
    for p_i, a in enumerate(page_a_list):
        a_text = str(a.text)
        if a_text == next_ten_btn_text:
            next_ten_btn = a
        if a_text.startswith(' '):
            current_page_btn_index = p_i
    # print(current_page_btn_index, next_ten_btn)
    if current_page_btn_index is None:
        return None
    current_page_btn = page_a_list[current_page_btn_index]
    current_page_btn_text = str(current_page_btn.text).strip()
    current_page_btn_text_int = int(current_page_btn_text)
    if current_page_btn_text_int % 10 == 0:
        # 翻页器当前十页已到尾部，该翻下一页翻页器了
        return next_ten_btn
    else:
        # 翻页器未到当前第十页
        if next_ten_btn is not None:
            # 翻页器还未翻完
            return page_a_list[current_page_btn_index + 1]
        else:
            # 没有翻页器或翻页器已翻完
            # print('000')
            if current_page_btn_index + 1 < len(page_a_list):
                temp_next_btn = page_a_list[current_page_btn_index + 1]
                temp_next_btn_text = temp_next_btn.text
                if str(temp_next_btn_text).strip().isdigit():
                    return temp_next_btn
                else:
                    return None


def auto_next_page_apply(func):
    """
    自动翻页
    :param func:
    :param args:
    :return:
    """
    while True:
        if callable(func):
            try:
                func()
            except Exception as e:
                print(e)
                print('exception!!!')
                break
            # time.sleep(2)
        next_page_btn = find_next_page_btn()
        if next_page_btn is not None:
            print(next_page_btn.text)
            next_page_btn.click()
        else:
            # time.sleep(5)
            print('current pages over', func.__name__)
            break


In [7]:
page_size = 200

In [8]:
kw_dir_path = dir_path / '_'

In [9]:
def go_back():
    """
    回到上一页
    :return:
    """
    back_btn = driver.find_element_by_xpath('//div[@class="volver-btn"]')
    back_btn.click()
    time.sleep(0.3)


In [10]:
def collect_data():
    """
    收集数据
    :return:
    """
    tr_xpath = '//table[@id="tabla_resultados"]//tr'
    # tr_xpath = '//table[@id="contenido_result"]//tr'
    aggr_tr_list = driver.find_elements_by_xpath(tr_xpath)
    # print(aggr_tr_list)
    aggr_title_list = list()
    aggr_tr_list_len = len(aggr_tr_list)

    if aggr_tr_list_len <= 3:
        # 无数据
        print('this list is no data')

    for n in range(aggr_tr_list_len - 3):
        if n > page_size:
            break

        time.sleep(0.1)
        aggr_tr_list = driver.find_elements_by_xpath(tr_xpath)
        if len(aggr_tr_list) == 0:
            print('retry collect tr...')
            driver.refresh()
            time.sleep(1)
            aggr_tr_list = driver.find_elements_by_xpath(tr_xpath)
        aggr_tr_list = aggr_tr_list[2:-1]
        if len(aggr_tr_list) == 0 or n >= len(aggr_tr_list):
            break
        # time.sleep(0.1)
        print(search_hs_code_prefix, n, len(aggr_tr_list))

        # if len(aggr_tr_list) == 0:
        #     continue
        aggr_tr = aggr_tr_list[n]
        if n == 0:
            th_list = aggr_tr.find_elements_by_tag_name('th')
            aggr_title_list = list(map(lambda x: x.text, th_list[2:]))
        else:
            td_list = aggr_tr.find_elements_by_tag_name('td')
            # print(td_list)
            aggr_value_list = list(map(lambda x: x.text, td_list[2:]))

            sub_dir_path = kw_dir_path / str(aggr_value_list[0]).replace('?', '_')
            sub_dir_path.mkdir(exist_ok=True)

            flag_file_path = sub_dir_path / over_file
            if flag_file_path.exists():
                print(aggr_value_list[0])
                continue

            td_list[0].click()
            time.sleep(0.3)

            # 已进入详情页
            def collect_detail_data():
                """
                收集详细数据
                :return:
                """
                detail_a_list = driver.find_elements_by_xpath('//table[@id="tabla_resultados"]//tr/td/a[@class="open"]')
                # print(detail_a_list)
                for iai, item_a in enumerate(detail_a_list):
                    driver.execute_script("arguments[0].click();", item_a)
                    # item_a.click()
                    time.sleep(1.5)

                    # 抽取数据
                    modal_tr_list = driver.find_elements_by_xpath('//div[@id="contenedor"]//tr')
                    # print(modal_tr_list)
                    detail_data_info = list()
                    for modal_tr in modal_tr_list:
                        tr_td_list = modal_tr.find_elements_by_xpath('.//td')
                        # print(len(tr_td_list))
                        if len(tr_td_list) == 2:
                            detail_k = tr_td_list[0].text
                            detail_v = tr_td_list[1].text
                            detail_data_info.append({
                                'k': detail_k,
                                'v': detail_v
                            })
                    # print(detail_data_info)
                    for a_k, a_v in zip(aggr_title_list, aggr_value_list):
                        detail_data_info.append({
                            'a_k': a_k,
                            'a_v': a_v
                        })
                    file_path = sub_dir_path / f'{search_hs_code_prefix}_{datetime.datetime.now().strftime("%Y%m%d%H%M%S%f")}.json'
                    with open(file_path.as_posix(), 'w', encoding='utf8') as fp:
                        json.dump(detail_data_info, fp)

                    if iai == len(detail_a_list) - 1:
                        over_file_path = sub_dir_path / over_file
                        with open(over_file_path, 'w', encoding='utf8') as fp:
                            fp.write(' ')
                    print(file_path.as_posix())
                    time.sleep(0.3)
                    ActionChains(driver).send_keys(Keys.ESCAPE).perform()
                    # break


            auto_next_page_apply(collect_detail_data)

            # 详情页解析完毕
            # time.sleep(0.3)
            ActionChains(driver).send_keys(Keys.ESCAPE).perform()
            # time.sleep(0.2)
            go_back()
            # time.sleep(0.3)

        # print(aggr_title_list)

        # if n >= 1:
        #     break

# collect_data()




In [11]:
# 阿根廷（进出口）
def start():
    """
    开始入口
    :return:
    """
    # prefix_list = list(range(10))
    prefix_list = list(range(100))
    prefix_list = reversed(prefix_list)
    for kw_i in prefix_list:
        global search_hs_code_prefix
        # search_hs_code_prefix = f'{kw_i}%'
        search_hs_code_prefix = f'{kw_i:02}'
        global kw_dir_path
        kw_dir_path = dir_path / search_hs_code_prefix
        kw_dir_path.mkdir(exist_ok=True)

        search_input = driver.find_element_by_xpath('//input[@id="pos1"]')
        search_input.clear()
        search_input.send_keys(search_hs_code_prefix)

        # 起始月份
        search_month_input = driver.find_element_by_xpath('//select[@id="fecha1_2"]')
        Select(search_month_input).select_by_value(f'{month_start}')

        # 结束月份
        search_month_input = driver.find_element_by_xpath('//select[@id="fecha2_2"]')
        Select(search_month_input).select_by_value(f'{month_end}')

        search_btn = driver.find_element_by_xpath('//div[@id="btns"]/a')
        search_btn.click()

        try:
            # 设置分页大小
            page_size_select = driver.find_element_by_xpath('//select[@id="select_paginas"]')
            Select(page_size_select).select_by_value(f'{page_size}')
            time.sleep(1)

            auto_next_page_apply(collect_data)
        except Exception as e:
            print(e, 'apply')
        time.sleep(1)
        try:
            go_back()
        except Exception as e:
            print(e, 'start')

        # break


In [ ]:
while True:
    try:
        driver.get(edit_url)
        start()
    except Exception as e:
        print(e)

# driver.refresh()

Message: no such element: Unable to locate element: {"method":"xpath","selector":"//select[@id="select_paginas"]"}
  (Session info: chrome=96.0.4664.45)
 apply
Message: no such element: Unable to locate element: {"method":"xpath","selector":"//select[@id="select_paginas"]"}
  (Session info: chrome=96.0.4664.45)
 apply
97 0 9
retry collect tr...
97 1 9
  9701.10.20.00
97 2 9
  9703.00.00.00
97 3 9
  9701.90.20.00
97 4 9
  9701.10.10.00
97 5 9
  9701.90.10.00
97 6 9
  9702.00.00.00
97 7 9
  9704.00.00.00
97 8 9
list index out of range
exception!!!
96 0 80
96 1 80
  9607.19.00.00
96 2 80
  9603.40.00.00
96 3 80
  9616.10.00.00
96 4 80
  9608.10.00.00
96 5 80
  9615.90.00.00
96 6 80
  9603.90.90.00
96 7 80
  9608.20.00.00
96 8 80
  9617.00.00.00
96 9 80
  9619.00.29.00
96 10 80
  9615.11.00.00
96 11 80
  9609.10.10.00
96 12 80
  9618.00.00.00
96 13 80
E:/cobus_group/危地马拉/进口/202101_202109/96/  9603.29.00.00/96_20211129005419797192.json
E:/cobus_group/危地马拉/进口/202101_202109/96/  9603.29.00.00

In [ ]:
# tr_xpath = '//table[@id="tabla_resultados"]//tr'
# tr_xpath = '//table[@id="contenido_result"]//tr'
# aggr_tr_list = driver.find_elements_by_xpath(tr_xpath)

In [5]:
# for aggr_tr in aggr_tr_list:
#     print(aggr_tr)




[<selenium.webdriver.remote.webelement.WebElement (session="303660ab97574004e0d11f3c679d07fc", element="a370e2c6-9804-4dd9-b378-94b841e5d5f5")>,
 <selenium.webdriver.remote.webelement.WebElement (session="303660ab97574004e0d11f3c679d07fc", element="01b8dfed-8cee-4804-81fc-1c2982b85e2a")>,
 <selenium.webdriver.remote.webelement.WebElement (session="303660ab97574004e0d11f3c679d07fc", element="a5e33807-1040-4a03-aca1-4c02b570c83e")>,
 <selenium.webdriver.remote.webelement.WebElement (session="303660ab97574004e0d11f3c679d07fc", element="e8917375-13b0-44d7-905e-4100115fa5f9")>,
 <selenium.webdriver.remote.webelement.WebElement (session="303660ab97574004e0d11f3c679d07fc", element="754aef9a-75d1-471c-955b-e1926ac43cf1")>,
 <selenium.webdriver.remote.webelement.WebElement (session="303660ab97574004e0d11f3c679d07fc", element="f5d169c3-a7b2-4324-9cff-acde4d01eeb8")>,
 <selenium.webdriver.remote.webelement.WebElement (session="303660ab97574004e0d11f3c679d07fc", element="88068e06-1e1a-4c1c-8758-f1